# Unternehmensregister

## Fetch Auszug

In [1]:
import os
import glob

In [2]:
def wait_for_download_condition(
    path: str, num_files: int, pattern: str = "*.xml"
) -> bool:
    return len(glob.glob1(path, pattern)) > num_files


def get_num_files(path: str, pattern: str = "*.xml") -> int:
    return len(glob.glob1(path, pattern))


def rename_latest_file(path: str, filename: str, pattern: str = "*.xml"):
    list_of_files = [os.path.join(path, file) for file in glob.glob1(path, pattern)]
    latest_download = max(list_of_files, key=os.path.getctime)
    os.rename(latest_download, os.path.join(path, filename))

In [3]:
import os
from pathlib import Path

from selenium import webdriver


def configure_webdriver(
    headless: bool = True, download_dir: list[str] = ["data", "Unternehmensregister"]
) -> webdriver:
    options = webdriver.ChromeOptions()

    download_path = os.path.join(str(Path.cwd()), *download_dir)
    print(download_path)

    preferences = {
        "profile.default_content_settings.popups": 0,
        "safebrowsing.enabled": True,
        "download": {
            "directory_upgrade": True,
            "prompt_for_download": False,
            "extensions_to_open": "",
            "default_directory": download_path,
        },
    }
    if headless:
        options.add_argument("--headless=new")
    options.add_experimental_option("prefs", preferences)

    return webdriver.Chrome(options=options)

In [4]:
from tqdm import tqdm
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC


def scrape(driver, query: str, dir: str):
    driver.get("https://www.unternehmensregister.de/ureg/")
    # Accept Cookies
    driver.find_elements(
        By.XPATH, '//button[text()="Nur technisch notwendige Cookies akzeptieren"]'
    )[0].click()
    # Enter search query
    driver.find_elements(By.ID, "globalSearchForm:extendedResearchCompanyName")[
        0
    ].send_keys(query)
    # Trigger search
    driver.find_elements(By.ID, "globalSearchForm:btnExecuteSearchOld")[0].click()
    # Wait for results
    wait = WebDriverWait(driver, 5)
    wait.until(
        lambda driver: driver.current_url != "https://www.unternehmensregister.de/ureg/"
    )

    num_pages = int(
        driver.find_element(By.XPATH, '//*[@class="page_count"]').text.split(" ")[0]
    )

    processed_companies = []

    for page_index in tqdm(range(num_pages)):
        # Find all "Registerinformationen"
        companies_tab = driver.find_elements(
            By.LINK_TEXT, "Registerinformationen des Registergerichts"
        )
        company_names = [
            elem.text
            for elem in driver.find_elements(
                By.XPATH, '//div[@class="company_result"]/span/b'
            )
        ]
        for index, company_link in enumerate(companies_tab):
            company_name = company_names[index]
            if company_name in processed_companies:
                continue
            # Go to intermediary page
            company_link.click()
            # Trigger next redirect
            driver.find_element(By.LINK_TEXT, "Registerinformationen anzeigen").click()
            # Trigger SI download
            driver.find_element(By.LINK_TEXT, "SI").click()
            # Show shopping cart - TODO evaluate restructuring behaviour by filling cart first and then bulk downloading
            wait.until(
                EC.visibility_of_element_located(
                    (By.LINK_TEXT, "Dokumentenkorb ansehen")
                )
            )
            driver.find_element(By.LINK_TEXT, "Dokumentenkorb ansehen").click()
            # Get document
            xpath = "//input[@type='submit']"
            elems = driver.find_elements(By.TAG_NAME, "input")
            elems[-2].click()

            wait.until(
                EC.visibility_of_element_located((By.ID, "paymentFormOverview:btnNext"))
            )
            driver.find_element(By.ID, "paymentFormOverview:btnNext").click()

            wait.until(
                EC.visibility_of_element_located((By.LINK_TEXT, "Zum Dokumentenkorb"))
            )
            driver.find_element(By.LINK_TEXT, "Zum Dokumentenkorb").click()

            num_files = get_num_files(dir)
            driver.find_element(By.CLASS_NAME, "download-wrapper").click()

            try:
                wait.until(lambda x: wait_for_download_condition(dir, num_files))
                rename_latest_file(
                    dir,
                    f"{company_name.replace(' ', '_').replace('/','_')}.xml",
                )
                processed_companies.append(company_name)
            except:
                print(f"Could not process {company_name}")
            for i in range(6):
                driver.back()
        driver.find_element(By.XPATH, '//*[@class="fas fa-angle-right"]').click()
    driver.close()
    print(processed_companies)

In [5]:
import pandas as pd

df = pd.read_excel(
    "./data/study_id42887_top-100-unternehmen-deutschland.xlsx",
    sheet_name="Toplist",
    skiprows=1,
)
df.head()

Unnamed: 0                 Name IPO Status Exchange Listing ID  \
0          1           Volkswagen     PUBLIC     XETR       VOW3   
1          2  Mercedes-Benz Group     PUBLIC     XMUN        DAI   
2          3     Deutsche Telekom     PUBLIC     XFRA        DTE   
3          4                  Bmw     PUBLIC     XDUS       BMW3   
4          5        Deutsche Post     PUBLIC     XMUN        DPW   

   Founding Year                     ISIC Headquarters  \
0         1984.0    2910 - Motor Vehicles      Germany   
1         1987.0    2910 - Motor Vehicles      Germany   
2         1990.0  61 - Telecommunications      Germany   
3         1984.0    2910 - Motor Vehicles      Germany   
4         1989.0  5320 - Courier Services      Germany   

                        Street       City Postal Code            Phone  \
0              Berliner Ring 2  Wolfsburg       38440       +49-536190   
1          Mercedes Street 120  Stuttgart       70372   +49-7111795256   
2    Friedrich-Ebert-Allee 140       Bonn       53113   +49-2281814949   
3               Petuelring 130     Munich       80788   +49-8938224272   
4  Charles-De-Gaulle-Straße 20       Bonn       53113  +49-22818263636   

                       Website  Email End of fiscal year       2019  \
0         www.volkswagenag.com    NaN              12/31  282839.18   
1  www.group.mercedes-benz.com    NaN              12/31  193400.10   
2              www.telekom.com    NaN              12/31   90125.38   
3             www.bmwgroup.com    NaN              12/31  117613.06   
4          www.deutschepost.de    NaN              12/31   70914.68   

        2020       2021     CAGR*  Employees*  
0  254299.32  296086.81  0.020497    672800.0  
1  138942.51  158449.05 -0.071117    172425.0  
2  115235.87  128753.98  0.110871    216528.0  
3  113581.49  133364.51  0.048403    118909.0  
4   76119.57   96739.44  0.091205    592263.0

In [9]:
processes = []
for x in df.Name:
    search_query = x

    driver = configure_webdriver(
        download_dir=["data", "Unternehmensregister", search_query.strip()]
    )
    process = Process(
        target=scrape_process,
        args=(
            driver,
            search_query,
            f"./data/Unternehmensregister/{search_query.strip()}",
        ),
    )
    process.start()
    processes.append(process)

c:\Users\trist\Documents\Code\M.Sc\aki_prj23_transparenzregister\Jupyter\API-tests\Unternehmensregister\data\Unternehmensregister\Volkswagen


AttributeError: Can't pickle local object '_createenviron.<locals>.encodekey'

## Analyze Auszug

In [2]:
import os

num_files = 0
for folder in os.listdir("./data/Unternehmensregister/scraping/"):
    files = os.listdir("./data/Unternehmensregister/scraping/" + folder)
    num_files += len(files)
num_files

3405

In [1]:
import json
import glob
import xmltodict

In [3]:
def transform_xml_to_json(source_dir: str, target_dir: str):
    for source_path in [
        os.path.normpath(i) for i in glob.glob(source_dir + "**/*.xml", recursive=True)
    ]:
        print(source_path)
        target_path = os.path.join(
            target_dir, source_path.split("\\")[-1].replace(".xml", ".json")
        )

        with open(source_path, "r", encoding="utf-8") as source_file:
            try:
                data = xmltodict.parse(source_file.read().encode())
                with open(target_path, "w", encoding="utf-8") as json_file:
                    json_file.write(json.dumps(data))
            except:
                """"""


transform_xml_to_json(
    "./data/Unternehmensregister/scraping/", "./data/Unternehmensregister/export/"
)

data\Unternehmensregister\scraping\1&1\123fliegenfreiGmbH.xml
data\Unternehmensregister\scraping\1&1\1AAutenriethKunststofftechnikGmbHCoKG.xml
data\Unternehmensregister\scraping\1&1\1ABlumenGriesbaumInhPhilippZähringereK.xml
data\Unternehmensregister\scraping\1&1\1AlfdorferSolarbetriebsGmbHCoKG.xml
data\Unternehmensregister\scraping\1&1\1FreiburgerSolarfondsBeteiligungsKG.xml
data\Unternehmensregister\scraping\1&1\1GussMaulburgGmbH.xml
data\Unternehmensregister\scraping\1&1\1ServicesGmbH.xml
data\Unternehmensregister\scraping\1&1\1StaigerGrundstücksverwaltungGmbHCoKG.xml
data\Unternehmensregister\scraping\1&1\1stClassMarketingGmbH.xml
data\Unternehmensregister\scraping\1&1\1WeinheimerBestattungsunternehmeneGVereinigteWeinheimerHemsbacherSchreinermeister.xml
data\Unternehmensregister\scraping\Adidas\adidasAG.xml
data\Unternehmensregister\scraping\Adidas\adidasBeteiligungsgesellschaftmbH.xml
data\Unternehmensregister\scraping\Adidas\adidasCDCImmobilieninvestGmbH.xml
data\Unternehmensregi

In [4]:
from tqdm import tqdm

for file in tqdm(glob.glob1("./data/Unternehmensregister/", "*.json")):
    path = os.path.join("./data/Unternehmensregister/", file)
    with open(path, "r", encoding="utf-8") as file_object:
        data = json.loads(file_object.read())

0it [00:00, ?it/s]


In [1]:
import re
from aki_prj23_transparenzregister.models.company import Company


def parse_stakeholder(data: dict) -> list:
    if "Natuerliche_Person" in data["Beteiligter"]:
        return {
            "name": {
                "firstname": data["Beteiligter"]["Natuerliche_Person"]["Voller_Name"][
                    "Vorname"
                ],
                "lastname": data["Beteiligter"]["Natuerliche_Person"]["Voller_Name"][
                    "Nachname"
                ],
            },
            "date_of_birth": data["Beteiligter"]["Natuerliche_Person"]["Geburt"][
                "Geburtsdatum"
            ]
            if "Geburt" in data["Beteiligter"]["Natuerliche_Person"]
            else None,
            "location": {
                "city": data["Beteiligter"]["Natuerliche_Person"]["Anschrift"][-1][
                    "Ort"
                ]
                if type(data["Beteiligter"]["Natuerliche_Person"]["Anschrift"]) == list
                else data["Beteiligter"]["Natuerliche_Person"]["Anschrift"]["Ort"]
            },
            "role": data["Rolle"]["Rollenbezeichnung"]["content"],
        }
    if "Organisation" in data["Beteiligter"]:
        return {
            "role": "Organisation",
            "description": data["Beteiligter"]["Organisation"]["Bezeichnung"][
                "Bezeichnung_Aktuell"
            ],
            "location": {
                "city": data["Beteiligter"]["Organisation"]["Anschrift"]["Ort"],
                "street": data["Beteiligter"]["Organisation"]["Anschrift"]["Strasse"]
                if "Strasse" in data["Beteiligter"]["Organisation"]["Anschrift"]
                else None,
                "house_number": data["Beteiligter"]["Organisation"]["Anschrift"][
                    "Hausnummer"
                ]
                if "Hausnummer" in data["Beteiligter"]["Organisation"]["Anschrift"]
                else None,
                "zip_code": data["Beteiligter"]["Organisation"]["Anschrift"][
                    "Postleitzahl"
                ],
            },
        }


def loc_from_rechtstraeger(data: dict) -> dict:
    return {
        "city": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]["Ort"],
        "zip_code": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]["Postleitzahl"],
        "street": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]["Strasse"]
        if "Strasse"
        in data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]
        else None,
        "house_number": data["XJustiz_Daten"]["Fachdaten_Register"][
            "Basisdaten_Register"
        ]["Rechtstraeger"]["Anschrift"]["Hausnummer"]
        if "Hausnummer"
        in data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Anschrift"]
        else None,
    }


def loc_from_organisation(data: dict) -> dict:
    return {
        "city": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Organisation"
        ]["Anschrift"]["Ort"],
        "zip_code": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Organisation"
        ]["Anschrift"]["Postleitzahl"],
        "street": data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Organisation"
        ]["Anschrift"]["Strasse"]
        if "Strasse"
        in data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Organisation"
        ]["Anschrift"]
        else None,
        "house_number": data["XJustiz_Daten"]["Fachdaten_Register"][
            "Basisdaten_Register"
        ]["Organisation"]["Anschrift"]["Hausnummer"]
        if "Hausnummer"
        in data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Organisation"
        ]["Anschrift"]
        else None,
    }


def loc_from_beteiligung(data: dict) -> dict:
    return {
        "city": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][
            0
        ]["Beteiligter"]["Organisation"]["Anschrift"]["Ort"],
        "zip_code": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"][
            "Beteiligung"
        ][0]["Beteiligter"]["Organisation"]["Anschrift"]["Postleitzahl"],
        "street": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][
            0
        ]["Beteiligter"]["Organisation"]["Anschrift"]["Strasse"]
        if "Strasse"
        in data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][0][
            "Beteiligter"
        ]["Organisation"]["Anschrift"]
        else None,
        "house_number": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"][
            "Beteiligung"
        ][0]["Beteiligter"]["Organisation"]["Anschrift"]["Hausnummer"]
        if "Hausnummer"
        in data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][0][
            "Beteiligter"
        ]["Organisation"]["Anschrift"]
        else None,
    }


def name_from_rechtstraeger(data: dict) -> str:
    return data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
        "Rechtstraeger"
    ]["Bezeichnung"]["Bezeichnung_Aktuell"]


def name_from_organisation(data: dict) -> str:
    return data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
        "Organisation"
    ]["Bezeichnung"]["Bezeichnung_Aktuell"]


def name_from_beteiligung(data: dict) -> str:
    return data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][0][
        "Beteiligter"
    ]["Organisation"]["Bezeichnung"]["Bezeichnung_Aktuell"]


# TODO Not present in all companies - possibly map using name of company ...
def map_rechtsform(company_name: str, data: dict) -> str:
    try:
        return data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Rechtstraeger"
        ]["Rechtsform"]["content"]
    except:
        if (
            company_name.endswith("GmbH")
            or company_name.endswith("UG")
            or company_name.endswith("UG (haftungsbeschränkt)")
        ):
            return "Gesellschaft mit beschränkter Haftung"
        elif company_name.endswith("SE"):
            return "Europäische Aktiengesellschaft (SE)"
        elif company_name.endswith("KG"):
            return "Kommanditgesellschaft"
        return None


def map_stammkapital(data: dict, company_type: str) -> str:
    capital = {"Zahl": 0, "Waehrung": ""}
    if company_type == "Kommanditgesellschaft":
        if "Zusatzangaben" not in data["XJustiz_Daten"]["Fachdaten_Register"]:
            return None
        capital_type = "Hafteinlage"
        base = data["XJustiz_Daten"]["Fachdaten_Register"]["Zusatzangaben"][
            "Personengesellschaft"
        ]["Zusatz_KG"]["Daten_Kommanditist"]
        if type(base) == "list":
            for entry in base:
                # TODO link to persons using Ref_Rollennummer then extract ["Hafteinlage"] as below
                capital["Zahl"] = capital["Zahl"] + entry["Zahl"]
                # TODO Improve multi assignment
                capital["Waehrung"] = entry["Waehrung"]
        elif type(base) == "dict":
            capital = base["Hafteinlage"]
    elif company_type in [
        "Gesellschaft mit beschränkter Haftung",
        "Europäische Aktiengesellschaft (SE)",
        "Aktiengesellschaft",
        "Kommanditgesellschaft auf Aktien",
        "Rechtsform ausländischen Rechts HRB",
    ]:
        if "Zusatzangaben" not in data["XJustiz_Daten"]["Fachdaten_Register"]:
            return None
        if (
            "Zusatz_GmbH"
            in data["XJustiz_Daten"]["Fachdaten_Register"]["Zusatzangaben"][
                "Kapitalgesellschaft"
            ]
        ):
            capital_type = "Stammkapital"
            capital = data["XJustiz_Daten"]["Fachdaten_Register"]["Zusatzangaben"][
                "Kapitalgesellschaft"
            ]["Zusatz_GmbH"]["Stammkapital"]
        elif (
            "Zusatz_Aktiengesellschaft"
            in data["XJustiz_Daten"]["Fachdaten_Register"]["Zusatzangaben"][
                "Kapitalgesellschaft"
            ]
        ):
            capital_type = "Grundkapital"
            capital = data["XJustiz_Daten"]["Fachdaten_Register"]["Zusatzangaben"][
                "Kapitalgesellschaft"
            ]["Zusatz_Aktiengesellschaft"]["Grundkapital"]["Hoehe"]
    elif company_type in [
        "Einzelkaufmann",
        "Einzelkauffrau",
        "eingetragene Genossenschaft",
        "Partnerschaft",
        "Einzelkaufmann / Einzelkauffrau",
        "Offene Handelsgesellschaft",
        "Partnerschaftsgesellschaft",
        None,
    ]:
        return None
    else:
        return None
    return {
        "value": capital["Zahl"],
        "currency": capital["Waehrung"],
        "type": capital_type,
    }


def map_geschaeftszweck(data: dict) -> str:
    try:
        return data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Gegenstand_oder_Geschaeftszweck"
        ]
    except:
        return None


from datetime import datetime


def transform_date_to_iso(date: str) -> str:
    regex_yy = r"^\d{1,2}\.\d{1,2}\.\d{2}$"

    if re.match(regex_yy, date):
        input_format = "%d.%m.%y"
    else:
        input_format = "%d.%m.%Y"
    date_temp = datetime.strptime(date, input_format)
    return date_temp.strftime("%Y-%m-%d")


# TODO transform date to iso format (YYYY-MM-DD)
def map_founding_date(data: dict) -> str:
    text = str(data)
    entry_date = re.findall(
        r".Tag der ersten Eintragung:(\\n| )?(\d{1,2}\.\d{1,2}\.\d{2,4})", text
    )
    if len(entry_date) == 1:
        return transform_date_to_iso(entry_date[0][1])

    entry_date = re.findall(
        r".Gesellschaftsvertrag vom (\d{1,2}\.\d{1,2}\.\d{2,4})", text
    )
    if len(entry_date) == 1:
        return transform_date_to_iso(entry_date[0])

    if "Eintragungstext" in data["XJustiz_Daten"]["Fachdaten_Register"]["Auszug"]:
        if (
            type(
                data["XJustiz_Daten"]["Fachdaten_Register"]["Auszug"]["Eintragungstext"]
            )
            == "list"
        ):
            temp = data["XJustiz_Daten"]["Fachdaten_Register"]["Auszug"][
                "Eintragungstext"
            ][0]["Text"]
            results = re.findall(r"\d{1,2}\.\d{1,2}\.\d{2,4}", temp)
            if len(temp) == 1:
                return transform_date_to_iso(results[0])
    if (
        "Gruendungsmetadaten"
        in data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"]
    ):
        temp = data["XJustiz_Daten"]["Fachdaten_Register"]["Basisdaten_Register"][
            "Gruendungsmetadaten"
        ]["Gruendungsdatum"]
        return temp
    # No reliable answer
    # raise ValueError()
    return None


def map_unternehmensregister_json(data: dict) -> dict:
    result = {"relationships": []}

    # TODO Refactor mapping - this is a nightmare...
    result["id"] = {
        "hr_number": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"][
            "Instanzdaten"
        ]["Aktenzeichen"],
        "district_court": {
            "name": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"][
                "Beteiligung"
            ][1]["Beteiligter"]["Organisation"]["Bezeichnung"]["Bezeichnung_Aktuell"]
            if "Organisation"
            in data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][1][
                "Beteiligter"
            ]
            else data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][
                1
            ]["Beteiligter"]["Natuerliche_Person"]["Voller_Name"]["Nachname"],
            "city": data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"][
                "Beteiligung"
            ][1]["Beteiligter"]["Organisation"]["Sitz"]["Ort"]
            if "Organisation"
            in data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][1][
                "Beteiligter"
            ]
            else data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][
                1
            ]["Beteiligter"]["Natuerliche_Person"]["Anschrift"]["Ort"],
        },
    }
    result["name"] = name_from_beteiligung(data)

    result["location"] = loc_from_beteiligung(data)
    result["last_update"] = data["XJustiz_Daten"]["Fachdaten_Register"]["Auszug"][
        "letzte_Eintragung"
    ]
    # TODO New features --> to be tested
    result["company_type"] = map_rechtsform(result["name"], data)
    result["capital"] = map_stammkapital(data, result["company_type"])
    result["business_purpose"] = map_geschaeftszweck(data)
    result["founding_date"] = map_founding_date(data)

    for i in range(
        2, len(data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"])
    ):
        people = parse_stakeholder(
            data["XJustiz_Daten"]["Grunddaten"]["Verfahrensdaten"]["Beteiligung"][i]
        )
        result["relationships"].append(people)
    return Company(**result)

In [2]:
import os
import json
import glob
import dataclasses
from tqdm import tqdm

In [3]:
for file in tqdm(glob.glob1("./data/Unternehmensregister/export", "*.json")):
    path = os.path.join("./data/Unternehmensregister/export", file)
    with open(path, "r", encoding="utf-8") as file_object:
        print(path)
        data = json.loads(file_object.read())
        company: Company = map_unternehmensregister_json(data)

        name = "".join(e for e in company.name if e.isalnum())[:50]

        with open(
            f"./data/Unternehmensregister/transformed/{name}.json",
            "w+",
            encoding="utf-8",
        ) as export_file:
            json.dump(dataclasses.asdict(company), export_file, ensure_ascii=False)

  0%|          | 0/3381 [00:00<?, ?it/s]

  5%|▍         | 155/3381 [00:00<00:04, 805.91it/s]

./data/Unternehmensregister/export\01019TelefondiensteGmbH.json
./data/Unternehmensregister/export\01024TelefondiensteGmbH.json
./data/Unternehmensregister/export\01050comGmbH.json
./data/Unternehmensregister/export\11DeMailGmbH.json
./data/Unternehmensregister/export\11EnergyGmbH.json
./data/Unternehmensregister/export\11LogistikGmbH.json
./data/Unternehmensregister/export\11MailMediaApplicationsSE.json
./data/Unternehmensregister/export\11MailMediaDevelopmentTechnologyGmbH.json
./data/Unternehmensregister/export\11MailMediaGmbH.json
./data/Unternehmensregister/export\11MailMediaServiceGmbH.json
./data/Unternehmensregister/export\11TelecomGmbH.json
./data/Unternehmensregister/export\11TelecomHoldingGmbH.json
./data/Unternehmensregister/export\11TelecommunicationSE.json
./data/Unternehmensregister/export\11TelecomSalesGmbH.json
./data/Unternehmensregister/export\11TelecomServiceMontabaurGmbH.json
./data/Unternehmensregister/export\11TelecomServiceZweibrückenGmbH.json
./data/Unternehmen

  7%|▋         | 251/3381 [00:00<00:03, 874.31it/s]

./data/Unternehmensregister/export\AureliusDigitalVenturesUGhaftungsbeschränkt.json
./data/Unternehmensregister/export\AURELIUSEpsilonInternationalGmbH.json
./data/Unternehmensregister/export\AURELIUSEpsilonInvestGmbH.json
./data/Unternehmensregister/export\AURELIUSEquityOpportunitiesSECoKGaA.json
./data/Unternehmensregister/export\AURELIUSGammaInternationalGmbH.json
./data/Unternehmensregister/export\AURELIUSGammaInvestGmbH.json
./data/Unternehmensregister/export\AureliusGmbH.json
./data/Unternehmensregister/export\AureliusHofMainhausenGmbH.json
./data/Unternehmensregister/export\AureliusHoldingUGhaftungsbeschränkt.json
./data/Unternehmensregister/export\AureliusHorizonUGhaftungsbeschränkt.json
./data/Unternehmensregister/export\AureliusImmobiliengesellschaftAmFannyMendelssohnPlatzGmbHCoKG.json
./data/Unternehmensregister/export\AureliusImmobiliengesellschaftamUdoLindenbergPlatzGmbH.json
./data/Unternehmensregister/export\AureliusImmobilienGmbH.json
./data/Unternehmensregister/export\

...

./data/Unternehmensregister/export\SKIImmobilienBirgitSalzeK.json
./data/Unternehmensregister/export\SKInternationalBeteiligungenGmbH.json
./data/Unternehmensregister/export\SKIPDatentechnikGmbHSystemKonzepteFürInnovativeProdukte.json
./data/Unternehmensregister/export\SKIVerwaltungsGmbHSkikonstruktionsinstitut.json
./data/Unternehmensregister/export\SKManagementGmbH.json
./data/Unternehmensregister/export\SKManagementundBeteiligungsGmbH.json
./data/Unternehmensregister/export\SKMarineSuppliesGmbH.json
./data/Unternehmensregister/export\SKMetallverarbeitungVerwaltungsGmbH.json
./data/Unternehmensregister/export\SKMInformatikGmbH.json
./data/Unternehmensregister/export\SKPhysioServiceGmbHMeuselwitz.json
./data/Unternehmensregister/export\SKRetailGmbH.json
./data/Unternehmensregister/export\SKRobotertechnikGmbH.json
./data/Unternehmensregister/export\SKSauerundKrewettGmbH.json
./data/Unternehmensregister/export\SKSAutozubehörProdukteVertriebsGmbH.json
./data/Unternehmensregister/export\S

 95%|█████████▌| 3214/3381 [00:04<00:00, 766.50it/s]

./data/Unternehmensregister/export\TUIBeteiligungsGmbH.json
./data/Unternehmensregister/export\TUIBKK.json
./data/Unternehmensregister/export\TUIBLUEDEGmbH.json
./data/Unternehmensregister/export\TUIBusinessServicesGmbH.json
./data/Unternehmensregister/export\TUICruisesGmbH.json
./data/Unternehmensregister/export\TUICustomerOperationsGmbH.json
./data/Unternehmensregister/export\TUIDeutschlandGmbH.json
./data/Unternehmensregister/export\TUIflyGmbH.json
./data/Unternehmensregister/export\TUIflyVermarktungsGmbH.json
./data/Unternehmensregister/export\TUIGroupServicesGmbH.json
./data/Unternehmensregister/export\TUIHotelBetriebsgesellschaftmbH.json
./data/Unternehmensregister/export\TUIImmobilienServicesGmbH.json
./data/Unternehmensregister/export\TUIInfoTecGmbH.json
./data/Unternehmensregister/export\TUIInsuranceFinancialGmbH.json
./data/Unternehmensregister/export\TUILeisureTravelServiceGmbH.json
./data/Unternehmensregister/export\TUIReiseCenterJürgenJehleeK.json
./data/Unternehmensregist

100%|██████████| 3381/3381 [00:04<00:00, 750.57it/s]

./data/Unternehmensregister/export\VonoviaTechnischerServiceNordGmbH.json
./data/Unternehmensregister/export\VonoviaTechnischerServiceSüdGmbH.json
./data/Unternehmensregister/export\VonoviaWohnumfeldServiceGmbH.json
./data/Unternehmensregister/export\VULKANINOXGmbH.json
./data/Unternehmensregister/export\VWRInternationalGmbH.json
./data/Unternehmensregister/export\VWRInternationalImmobilienGmbH.json
./data/Unternehmensregister/export\WackerBiotechGmbH.json
./data/Unternehmensregister/export\WackerChemieAchteVentureGesellschaftmitbeschränkterHaftung.json
./data/Unternehmensregister/export\WackerChemieAG.json
./data/Unternehmensregister/export\WackerChemieElfteVentureGesellschaftmitbeschränkterHaftung.json
./data/Unternehmensregister/export\WackerChemieVersicherungsvermittlungGmbH.json
./data/Unternehmensregister/export\WackerChemieZwölfteVentureGesellschaftmitbeschränkterHaftung.json
./data/Unternehmensregister/export\WackerNeusonAftermarketServicesGmbH.json
./data/Unternehmensregister/

In [4]:
from aki_prj23_transparenzregister.utils.mongo.connector import (
    MongoConnector,
    MongoConnection,
)
from aki_prj23_transparenzregister.utils.mongo.company_mongo_service import (
    CompanyMongoService,
)

conn_string = MongoConnection(
    hostname="localhost",
    database="transparenzregister",
    username="username",
    password="password",
    port=27017,
)

connector = MongoConnector(conn_string)

service = CompanyMongoService(connector)

In [5]:
from tqdm import tqdm
import glob
import os
import json
from aki_prj23_transparenzregister.models.company import Company

num_inserted = 0
for file in tqdm(glob.glob1("./data/Unternehmensregister/transformed", "*.json")):
    path = os.path.join("./data/Unternehmensregister/transformed", file)
    with open(path, "r", encoding="utf-8") as file_object:
        data = json.loads(file_object.read())
        company: Company = Company(**data)

        company_db = service.get_by_id(company.id)
        if company_db is None:
            service.insert(company)
            num_inserted += 1
print(f"Inserted documents: {num_inserted}")

  0%|          | 0/3147 [00:00<?, ?it/s]

100%|██████████| 3147/3147 [00:32<00:00, 96.11it/s] 

Inserted documents: 3147
